In [225]:
import math 
import random
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd

Parametros algoritmo

In [226]:
Muta = 0.07 #Probabilidad de mutacion
N_padres = 150 #Numero de padres en la seleccion de cruces
N_Poblacion = 500 #Numero de individuos en la poblacion
GenMax = 500 #Número de generaciones max

In [227]:
Stream_Lit_Pres = 2300  #Resultado dado por Stream Lit, valor por defecto = 1500€

#Presupuesto del Arbol Genetico
#Restamos 90€ de fuente de alimentacion generica
#Restamos 70€ de caja generica
#Restamos 90€ de placa base
Presupuesto = Stream_Lit_Pres - 90 - 70 - 90

Uso = None
Uso = 'Ordenador de oficina'
#Uso = 'Ordenador de alto rendimiento'

Importacion de csv + info

In [228]:
CPU = pd.read_csv('cpu_ferran_clean.csv')
GPU = pd.read_csv('gpu_ferran_clean.csv')
SSD = pd.read_csv('SSD_limpio.csv')
RAM = pd.read_csv('RAM_clean.csv')
PS = pd.read_csv('power-supply_clean.csv')
CASE = pd.read_csv('case_clean.csv')
MB = pd.read_csv('motherboard_clean.csv')

print(f'CPU tiene {len(CPU)} lineas, GPU tiene {len(GPU)} lineas, SSD tiene {len(SSD)} lineas y RAM tiene {len(RAM)} lineas,')

CPU tiene 95 lineas, GPU tiene 850 lineas, SSD tiene 48 lineas y RAM tiene 1453 lineas,


In [229]:
Comp_total = len(CPU) + len(GPU) + len(SSD) + len(RAM)
print(f'Cantidad de componentes totales: {Comp_total}')

Cantidad de componentes totales: 2446


In [230]:
CPU.head(1)

Nombre  Precio  Numero_Procesamiento  Frecuencia_Maxima  \
0  Intel Core i9-14900KS  699.99                    24                6.2   

   Calor_Max_Teorico  SMT  Ranking  
0                150    1        1

In [231]:
GPU.head(1)

Fabricante   Precio              Chip  Memoria  Nucleo_Reloj  \
0  MSI VENTUS 3X E OC  2149.98  GeForce RTX 4090       24          2235   

   Impulsion_Reloj  Longitud  Ranking  
0             2565       322        1

In [232]:
SSD.head(1)

Nombre  Precio  Capacidad (GB)         Interfaz Fabricante  Rank
0  WD Black SN850X  279.99            4000  M.2 PCIe 4.0 X4         WD     1

In [233]:
pd.set_option('display.max_rows', 150)

In [234]:
RAM.head(1)

Nombre  Precio  Velocidad Modulos  Latencia  Tipo  \
0  G.Skill Trident Z5 RGB 48 GB  399.99       8400    2,24      40.0  DDR5   

   Cantidad_total  Rank  
0              48     1

# Selección tipos de uso

-Solo AMD AM4 G
-Presupuesto 600€

In [235]:
if Uso != None:
    if Uso == 'Ordenador de oficina':

        #Presupuesto del Arbol Genetico
    #Restamos 86€ de caja con fuente de alimentacion
    #Restamos 110€ de placa base
        Stream_Lit_Pres = 600
        Presupuesto = Stream_Lit_Pres - 86 - 110

# Funciones

Funcion de obtencion de genes para un cromosoma aleatoriamente

In [236]:
def RandomCrom (Crom_List = [], Pres = Presupuesto, CPU = CPU, GPU = GPU, SSD = SSD, RAM = RAM):

    Crom_List = []

    Total = 0

    while Total > Pres or Total == 0:
        
        CPU_Crom = random.randint(0,len(CPU)-1)
        if Uso != 'Ordenador de oficina':
            GPU_Crom = random.randint(0,len(GPU)-1)
        SSD_Crom = random.randint(0,len(SSD)-1)
        RAM_Crom = random.randint(0,len(RAM)-1)

        Total = CPU['Precio'][CPU_Crom] + SSD['Precio'][SSD_Crom]+ RAM['Precio'][RAM_Crom]

        if Uso != 'Ordenador de oficina':
            Total += GPU['Precio'][GPU_Crom]   

    Crom_List.append(CPU_Crom)
    if Uso != 'Ordenador de oficina':
        Crom_List.append(GPU_Crom)
    Crom_List.append(SSD_Crom)
    Crom_List.append(RAM_Crom)

    return Crom_List
    

Funcion de obtencion del ranking de cada gen dentro de un cromosoma

In [237]:
def RankCrom (crom_list : list, df_cpu = CPU, df_gpu = GPU, df_ssd = SSD, df_ram = RAM):

    Rank_List = []
    
    if Uso == 'Ordenador de oficina':

        Rank_List.append(df_cpu['Ranking'][crom_list[0]])        
        Rank_List.append(df_ssd['Rank'][crom_list[1]])
        Rank_List.append(df_ram['Rank'][crom_list[2]])

    else:

        Rank_List.append(df_cpu['Ranking'][crom_list[0]])    
        Rank_List.append(df_gpu['Ranking'][crom_list[1]])
        Rank_List.append(df_ssd['Rank'][crom_list[2]])
        Rank_List.append(df_ram['Rank'][crom_list[3]])

    return Rank_List

Funcion obtencion del fitness, en este caso la suma de los rankings (cuanto mas pequeño mejor)

In [238]:
def FitMaker(RankPob : list):

    Fitness_list = []

    for i in range(len(RankPob)):        

        Fitness_list.append(sum(RankPob[i]))

    return Fitness_list
    

Funcion obtencion de precio de cada cromosoma

In [239]:
def PrecioCrom(Pob : list):

    Precio_list = []

    for i in range(len(Pob)):

        Precio_cr = 0
        if Uso != 'Ordenador de oficina':
            for j in range(len(Pob[i])):
                            
                if j == 0:
                    Precio_cr += CPU['Precio'][Pob[i][j]]
                if j == 1:
                    Precio_cr += GPU['Precio'][Pob[i][j]]
                if j == 2:
                    Precio_cr += SSD['Precio'][Pob[i][j]]
                if j == 3:
                    Precio_cr += RAM['Precio'][Pob[i][j]]
        else:

            for j in range(len(Pob[i])):
                            
                if j == 0:
                    Precio_cr += CPU['Precio'][Pob[i][j]]
                if j == 1:
                    Precio_cr += SSD['Precio'][Pob[i][j]]
                if j == 2:
                    Precio_cr += RAM['Precio'][Pob[i][j]]
        
        Precio_list.append(round(Precio_cr,2))

    return Precio_list

Funcion obtencion hijos nuevos

In [240]:
def CruceNCromosomas(n = N_padres, Pob = [], i_padres = [], m = Muta):

    padres = []
    hijos_totales = []
    precio_hijos = []
    Precio_1 = []
    Precio_2 = []

    random.shuffle(i_padres)

    for i in range(0, len(i_padres), 2):     # Primero creamos las parejas 

        padres.append([i_padres[i], i_padres[i+1]])        

    for j in range(len(padres)):    #Creacion de nuevos hijos mediante cruce homogeneo (intercambiamos)

        hijo_1 = []
        hijo_2 = []

        lista_aux = Pob[padres[j][0]]

        for k in range(len(Pob[padres[j][0]])):

            if k % 2 == 0:
                
                hijo_1.append(Pob[padres[j][0]][k])
                hijo_2.append(Pob[padres[j][1]][k])

            else:

                hijo_1.append(Pob[padres[j][1]][k])
                hijo_2.append(Pob[padres[j][0]][k])


        if random.random() < m: #Calculamos aleatoriamente si muta o no
            
            nrandom = random.randint(0,len(hijo_1)-1)
            Crom_random = RandomCrom()

            hijo_1[nrandom] = Crom_random[nrandom]
        
        if random.random() < m: #Calculamos aleatoriamente si muta o no
            
            nrandom = random.randint(0,len(hijo_2)-1)
            Crom_random = RandomCrom()

            hijo_2[nrandom] = Crom_random[nrandom]
        
        Precio_1 = []
        Precio_2 = []
        aux1 = []
        aux2 = []

        aux1.append(hijo_1)
        aux2.append(hijo_2)

        Precio_1 = PrecioCrom(aux1)
        Precio_2 = PrecioCrom(aux2)
        
        if Precio_1[0] < Presupuesto:
            hijos_totales.append(hijo_1)
            precio_hijos.append(Precio_1[0])


        if Precio_2[0] < Presupuesto:
           hijos_totales.append(hijo_2)
           precio_hijos.append(Precio_2[0])


    return hijos_totales

# Obtencion de poblacion inicial (N Cromosomas, Valor total < Presupuesto)

In [241]:
Poblacion = []
Rank_Poblacion = []
Precio_Poblacion = []

for i in range(N_Poblacion):

    Cromosoma = RandomCrom()
    Rank_Cromosoma = RankCrom(Cromosoma)

    Poblacion.append(Cromosoma)
    Rank_Poblacion.append(Rank_Cromosoma)

Precio = PrecioCrom(Poblacion)
Fitness = FitMaker(Rank_Poblacion)

print('Poblacion:')
print(Poblacion)
print('-'*200)

print('Ranking poblacion:')
print(Rank_Poblacion)
print('-'*200)

print('Fitness:')
print(Fitness)
print('-'*200)

print('Precio:')
print(Precio)
print('-'*200)

Poblacion:
[[62, 31, 49], [88, 20, 957], [77, 20, 965], [61, 46, 477], [81, 10, 654], [70, 10, 1051], [93, 28, 754], [49, 40, 722], [56, 10, 309], [39, 23, 1011], [94, 30, 74], [35, 21, 467], [37, 43, 1307], [72, 35, 1380], [60, 9, 288], [89, 13, 1335], [83, 45, 717], [90, 28, 1071], [40, 16, 346], [55, 7, 1348], [75, 23, 993], [81, 31, 114], [70, 28, 508], [88, 27, 679], [60, 47, 992], [93, 39, 127], [93, 42, 888], [63, 45, 729], [71, 47, 1277], [89, 36, 1302], [67, 21, 649], [42, 40, 1260], [56, 14, 883], [56, 27, 907], [79, 36, 1319], [81, 13, 1313], [36, 8, 1198], [93, 10, 477], [36, 6, 884], [65, 36, 1322], [33, 23, 1365], [70, 18, 577], [71, 18, 1361], [88, 33, 1347], [65, 31, 1228], [89, 10, 1443], [92, 44, 38], [40, 12, 945], [81, 28, 759], [60, 44, 1332], [35, 36, 968], [60, 47, 330], [81, 20, 210], [70, 17, 291], [49, 44, 1335], [70, 9, 729], [71, 4, 1331], [56, 14, 1203], [93, 16, 494], [93, 6, 1222], [93, 41, 184], [60, 39, 1073], [79, 42, 493], [90, 46, 1386], [65, 30, 461

In [242]:
Fitness_inicial = FitMaker(Poblacion)
print(Fitness_inicial)

[142, 1065, 1062, 584, 745, 1131, 875, 811, 375, 1073, 198, 523, 1387, 1487, 357, 1437, 845, 1189, 402, 1410, 1091, 226, 606, 794, 1099, 259, 1023, 837, 1395, 1427, 737, 1342, 953, 990, 1434, 1407, 1242, 580, 926, 1423, 1421, 665, 1450, 1468, 1324, 1542, 174, 997, 868, 1436, 1039, 437, 311, 378, 1428, 808, 1406, 1273, 603, 1321, 318, 1172, 614, 1522, 556, 304, 976, 769, 1324, 1392, 791, 1340, 1357, 213, 1179, 439, 1252, 627, 1403, 1326, 1377, 1044, 1174, 1456, 373, 390, 865, 1380, 1304, 777, 345, 1266, 993, 1420, 136, 543, 1444, 960, 1347, 1324, 1391, 1409, 1214, 367, 577, 183, 1515, 261, 682, 1316, 725, 709, 1361, 1492, 1491, 1458, 1463, 998, 482, 867, 1409, 850, 1484, 1041, 934, 540, 719, 1360, 944, 854, 1068, 706, 1179, 1101, 1410, 222, 1333, 1403, 1454, 1381, 994, 198, 1418, 1379, 1036, 1104, 1466, 1008, 1545, 655, 630, 654, 1107, 1101, 992, 372, 1326, 949, 1251, 1066, 1403, 261, 549, 1454, 1339, 461, 278, 1133, 658, 857, 1383, 1015, 118, 572, 200, 302, 1349, 1076, 692, 673, 543, 5

# Cruce de poblacion

In [243]:
for Gen in range(GenMax):
    # Obtenemos los N_padres valores más grandes junto con sus índices
    Cromosomas_Padre = []

    for posicion, valor in enumerate(Poblacion):

        if len(Cromosomas_Padre) < N_padres:    # Llenamos primero la lista con los N_padres primeros cromosomas

            Cromosomas_Padre.append((valor, posicion))

        else:
            
            maximo_actual, max_posicion = min(Cromosomas_Padre) # Si ya tenemos N_padres valores, comparamos con el mínimo actual

            if valor < maximo_actual:

                Cromosomas_Padre.remove((maximo_actual, max_posicion))
                Cromosomas_Padre.append((valor, posicion))

    indices_Cromosomas_Padre = [posicion for _, posicion in Cromosomas_Padre]   # Extraemos solo los índices de los valores más grandes

    print('Generacion:')
    print(Gen)
    print('-'*200)
    print('Poblacion:')
    print(Poblacion)
    print('-'*200)
    print(f"Índices de los {N_padres} con un Fitness mas alto:")
    print(indices_Cromosomas_Padre)

    Hijos = CruceNCromosomas(Pob = Poblacion, i_padres = indices_Cromosomas_Padre)

    print('-'*200)
    print('Hijos:')
    print(Hijos)
    print('-'*200)

    Poblacion_Nueva = []
    indices_Poblacion_Nueva = []

    Poblacion.extend(Hijos)

    for posicion, valor in enumerate(Poblacion):

        if len(Poblacion_Nueva) < N_Poblacion:    # Llenamos primero la lista con los N_Poblacion primeros individuos

            Poblacion_Nueva.append(valor)
            indices_Poblacion_Nueva.append(posicion)

        else:
            
            maximo_actual = min(Poblacion_Nueva) # Si ya tenemos N_Poblacion valores, comparamos con el mínimo actual
            max_posicion = indices_Poblacion_Nueva[Poblacion_Nueva.index(maximo_actual)]
        

            if valor < maximo_actual:

                Poblacion_Nueva.remove(maximo_actual)
                indices_Poblacion_Nueva.remove(max_posicion)
                Poblacion_Nueva.append(valor)
                indices_Poblacion_Nueva.append(posicion)

    Poblacion = Poblacion_Nueva
    print(f"Índices de los {N_Poblacion} cromosomas con un Fitness mas alto:")
    print(indices_Poblacion_Nueva)
    print('-'*200)

Fitness_Total = FitMaker(Poblacion)
print(Fitness_Total)

Generacion:
0
--------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------
Poblacion:
[[62, 31, 49], [88, 20, 957], [77, 20, 965], [61, 46, 477], [81, 10, 654], [70, 10, 1051], [93, 28, 754], [49, 40, 722], [56, 10, 309], [39, 23, 1011], [94, 30, 74], [35, 21, 467], [37, 43, 1307], [72, 35, 1380], [60, 9, 288], [89, 13, 1335], [83, 45, 717], [90, 28, 1071], [40, 16, 346], [55, 7, 1348], [75, 23, 993], [81, 31, 114], [70, 28, 508], [88, 27, 679], [60, 47, 992], [93, 39, 127], [93, 42, 888], [63, 45, 729], [71, 47, 1277], [89, 36, 1302], [67, 21, 649], [42, 40, 1260], [56, 14, 883], [56, 27, 907], [79, 36, 1319], [81, 13, 1313], [36, 8, 1198], [93, 10, 477], [36, 6, 884], [65, 36, 1322], [33, 23, 1365], [70, 18, 577], [71, 18, 1361], [88, 33, 1347], [65, 31, 1228], [89, 10, 1443], [92, 44, 38], [40, 12, 945], [81, 28, 759], [60, 44, 1332], [35, 36, 9

Generacion:
25
--------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------
Poblacion:
[[62, 31, 49], [88, 20, 957], [77, 20, 965], [61, 46, 477], [81, 10, 654], [70, 10, 1051], [93, 28, 754], [49, 40, 722], [56, 10, 309], [39, 23, 1011], [94, 30, 74], [35, 21, 467], [37, 43, 1307], [72, 35, 1380], [60, 9, 288], [89, 13, 1335], [83, 45, 717], [90, 28, 1071], [40, 16, 346], [55, 7, 1348], [75, 23, 993], [81, 31, 114], [70, 28, 508], [88, 27, 679], [60, 47, 992], [93, 39, 127], [93, 42, 888], [63, 45, 729], [71, 47, 1277], [89, 36, 1302], [67, 21, 649], [42, 40, 1260], [56, 14, 883], [56, 27, 907], [79, 36, 1319], [81, 13, 1313], [36, 8, 1198], [93, 10, 477], [36, 6, 884], [65, 36, 1322], [33, 23, 1365], [70, 18, 577], [71, 18, 1361], [88, 33, 1347], [65, 31, 1228], [89, 10, 1443], [92, 44, 38], [40, 12, 945], [81, 28, 759], [60, 44, 1332], [35, 36, 

# Resultado del Algoritmo Genetico

In [244]:
print(MB['Nombre'][241], MB['Precio'][241], '€')
print(MB['Nombre'][62], MB['Precio'][62], '€')
print(MB['Nombre'][76], MB['Precio'][76], '€')
print(MB['Nombre'][191], MB['Precio'][191], '€')


ASRock B550 Phantom Gaming 4 89.99 €
Gigabyte B650M D3HP 109.99 €
MSI PRO B760M-P DDR4 89.99 €
Gigabyte H510M K V2 86.13 €


In [245]:
#Ordenador alto rendimiento
Cpu_zocalo = None

if Uso != 'Ordenador de oficina':
    Target = Poblacion[Fitness_Total.index(min(Fitness_Total))]
    Fitness_optimizado = Fitness_Total[Fitness_Total.index(min(Fitness_Total))]
    indice_optimizado = Fitness_Total.index(min(Fitness_Total))

    if GPU['Chip'][Target[1]] == 'GeForce RTX 4090' or GPU['Chip'][Target[1]] == 'Radeon RX 7900 XTX':
        F_Alim = 62
    else:
        F_Alim = 166

    #Se compara el nombre de la cpu y se mira el zocalo, luego añadimos una placa base para ese zocalo
    cpu_nombre = CPU['Nombre'][Target[0]]
    while Cpu_zocalo == None:
        if 'AMD' in cpu_nombre.split(' Ryzen ')[0]:        
            if ' 7' in cpu_nombre.split(' Ryzen ')[1] or ' 8' in cpu_nombre.split(' Ryzen ')[1]:
                Cpu_zocalo, Mb_ex = 'AM5', 62
            elif ' 5' in cpu_nombre.split(' Ryzen ')[1]:
                if RAM['Tipo'][Target[3]] == 'DDR5':
                    Poblacion.pop(Fitness_Total.index(min(Fitness_Total)))
                    Fitness_Total.pop(Fitness_Total.index(min(Fitness_Total)))
                    
                    Target = Poblacion[Fitness_Total.index(min(Fitness_Total))]
                    Fitness_optimizado = Fitness_Total[Fitness_Total.index(min(Fitness_Total))]
                    indice_optimizado = Fitness_Total.index(min(Fitness_Total))
                    
                    cpu_nombre = CPU['Nombre'][Target[0]]
                else:
                    Cpu_zocalo, Mb_ex = 'AM4', 241

        elif 'Intel' in cpu_nombre.split('-')[0]:
            if '10' in cpu_nombre or '11' in cpu_nombre:
                Cpu_zocalo, Mb_ex = 'LGA1200', 191
                if RAM['Tipo'][Target[3]] == 'DDR5':
                    Poblacion.pop(Fitness_Total.index(min(Fitness_Total)))
                    Fitness_Total.pop(Fitness_Total.index(min(Fitness_Total)))
                    
                    Target = Poblacion[Fitness_Total.index(min(Fitness_Total))]
                    Fitness_optimizado = Fitness_Total[Fitness_Total.index(min(Fitness_Total))]
                    indice_optimizado = Fitness_Total.index(min(Fitness_Total))
                    
                    cpu_nombre = CPU['Nombre'][Target[0]]

            elif '12' in cpu_nombre.split('-')[1] or '13' in cpu_nombre.split('-')[1] or '14' in cpu_nombre.split('-')[1]:
                
                if RAM['Tipo'][Target[3]] == 'DDR5':
                    Cpu_zocalo, Mb_ex = 'LGA1700', 86
                else:
                    Cpu_zocalo, Mb_ex = 'LGA1700', 76

    print('Cromosoma optimo:', Target)
    print('Fitness del cromosoma:', Fitness_optimizado)

    print('-'*50)
    print('Procesador:', CPU['Nombre'][Target[0]], f"{CPU['Precio'][Target[0]]}€")
    print('Targeta Grafica:', GPU['Fabricante'][Target[1]], GPU['Chip'][Target[1]], f"{GPU['Precio'][Target[1]]}€")
    print('Almacenamiento SSD', SSD['Nombre'][Target[2]], f"{SSD['Capacidad (GB)'][Target[2]]} GB", SSD['Interfaz'][Target[2]], f"{SSD['Precio'][Target[2]]}€")
    print('Memoria RAM:', RAM['Nombre'][Target[3]], f"{RAM['Velocidad'][Target[3]]} MHz", f"{RAM['Tipo'][Target[3]]}", f"{RAM['Precio'][Target[3]]}€")
    print('-'*50)
    print(f"Fuente de alimentación: {PS['Nombre'][F_Alim]}, {PS['Precio'][F_Alim]} €")
    print(f"Caja: {CASE['Nombre'][4]}, {CASE['Precio'][4]} €")
    print(f"Placa base: {MB['Nombre'][Mb_ex]} {Cpu_zocalo}, {MB['Precio'][Mb_ex]} €")
    print('-'*50)

    print(f"Precio: {round(PrecioCrom(Poblacion)[indice_optimizado] + PS['Precio'][F_Alim] + CASE['Precio'][0] + MB['Precio'][Mb_ex], 2)}€ de {Stream_Lit_Pres}€ disponibles")
    print(f'Tipo de uso {Uso}')
    

#Ordenador de Oficina
elif Uso == 'Ordenador de oficina':

    Target = Poblacion[Fitness_Total.index(min(Fitness_Total))]
    Fitness_optimizado = Fitness_Total[Fitness_Total.index(min(Fitness_Total))]
    indice_optimizado = Fitness_Total.index(min(Fitness_Total))

    cpu_nombre = CPU['Nombre'][Target[0]]

    while Cpu_zocalo != 'AM5':
        
        if 'AMD' in cpu_nombre.split(' Ryzen ')[0]:
        
            if ' 7' in cpu_nombre.split(' Ryzen ')[1] or ' 8' in cpu_nombre.split(' Ryzen ')[1]:
                
                Cpu_zocalo, Mb_ex = 'AM5', 62
            else:
           
                Poblacion.pop(Fitness_Total.index(min(Fitness_Total)))
                Fitness_Total.pop(Fitness_Total.index(min(Fitness_Total)))
                
                Target = Poblacion[Fitness_Total.index(min(Fitness_Total))]
                Fitness_optimizado = Fitness_Total[Fitness_Total.index(min(Fitness_Total))]
                indice_optimizado = Fitness_Total.index(min(Fitness_Total))
                
                cpu_nombre = CPU['Nombre'][Target[0]]

        else:
           
            Poblacion.pop(Fitness_Total.index(min(Fitness_Total)))
            Fitness_Total.pop(Fitness_Total.index(min(Fitness_Total)))
            
            Target = Poblacion[Fitness_Total.index(min(Fitness_Total))]
            Fitness_optimizado = Fitness_Total[Fitness_Total.index(min(Fitness_Total))]
            indice_optimizado = Fitness_Total.index(min(Fitness_Total))
            
            cpu_nombre = CPU['Nombre'][Target[0]]

        
            


    print('Cromosoma optimo:', Target)
    print('Fitness del cromosoma:', Fitness_optimizado)

    print('-'*50)
    print('Procesador:', CPU['Nombre'][Target[0]], f"{CPU['Precio'][Target[0]]}€")
    
    print('Almacenamiento SSD', SSD['Nombre'][Target[1]], f"{SSD['Capacidad (GB)'][Target[1]]} GB", SSD['Interfaz'][Target[1]], f"{SSD['Precio'][Target[1]]}€")
    print('Memoria RAM:', RAM['Nombre'][Target[2]], f"{RAM['Velocidad'][Target[2]]} MHz", f"{RAM['Tipo'][Target[2]]}", f"{RAM['Precio'][Target[2]]}€")
    print('-'*50)
    print(f"Caja: {CASE['Nombre'][658]}, {CASE['Precio'][658]} €")
    print(f"Placa base: {MB['Nombre'][Mb_ex]} {Cpu_zocalo}, {MB['Precio'][Mb_ex]} €")
    print('-'*50)

    print(f"Precio: {round(PrecioCrom(Poblacion)[indice_optimizado] + CASE['Precio'][0] + MB['Precio'][Mb_ex], 2)}€ de {Stream_Lit_Pres}€ disponibles")
    print(f'Tipo de uso {Uso}')






Cromosoma optimo: [82, 32, 86]
Fitness del cromosoma: 200
--------------------------------------------------
Procesador: AMD Ryzen 5 8600G 228.99€
Almacenamiento SSD Samsung 970 Evo Plus 250 GB M.2 PCIe 3.0 X4 64.98€
Memoria RAM: Mushkin Redline ST 32 GB 6800 MHz DDR5 105.98€
--------------------------------------------------
Caja: Apex TX-606-U3, 84.35 €
Placa base: Gigabyte B650M D3HP AM5, 109.99 €
--------------------------------------------------
Precio: 599.93€ de 600€ disponibles
Tipo de uso Ordenador de oficina
